In [1]:
import pandas as pd
import numpy as np

We explored the error file in `EDA-DL-0-1.ipynb` and saved a CSV of the failed download records, as it was not clear how we could potentially find those images from their Zenodo records (they didn't seem to be present in the records whose metadata listed them). There seem to be only 23 specimens that were not otherwise represented in our download.

## Explore Downloaded Images

We'll do an inner merge on the master file and checksums to get a master downloadable file, which will be further reduced to just unique images.

In [2]:
checksums = pd.read_csv("../metadata/deduplication/Jiggins_Zenodo_Img_Master_3477891Patch_checksums.csv", low_memory=False)
checksums.shape

(42143, 3)

In [3]:
checksums.nunique()

filepath    42143
filename    42143
md5         36212
dtype: int64

Difference between these is the number of unique Image names among the duplicated images. 

In [4]:
master = pd.read_csv("../metadata/Jiggins_Zenodo_Img_Master_3477891Patch.csv", low_memory = False)
master.shape

(44809, 28)

`filename` in `checksums` is `<X>_<Image_name>`, so we'll create such a `filename` column in `master` to merge the two DataFrames on.

In [5]:
master["filename"] = master["X"].astype(str) + "_" + master["Image_name"]
master.nunique()

CAMID               11991
X                   44809
Image_name          36281
View                    7
zenodo_name            33
zenodo_link            30
Sequence            10905
Taxonomic_Name        366
Locality              645
Sample_accession     1559
Collected_by           12
Other_ID             3081
Date                  807
Dataset                 8
Store                 137
Brood                 224
Death_Date             81
Cross_Type             30
Stage                   1
Sex                     3
Unit_Type               4
file_type               3
record_number          30
species               246
subspecies            155
genus                  94
file_url            39297
hybrid_stat             2
filename            44809
dtype: int64

Our number of unique downloaded images is 69 less than the number of unique values of `Image_name`. For reference, we recorded 612 unique `CAMID`s in our error log of 2666 images that could not be downloaded.

### Merge `master` and `checksums`

In [7]:
master_checksums = pd.merge(master,
                            checksums,
                            on = "filename",
                            how = "inner")
# Expectation is 42143 entries now
master_checksums.shape

(42143, 31)

In [25]:
id_cols = ["CAMID", "Image_name", "X", "filename", "md5", "file_url"]
master_checksums[id_cols].nunique()

CAMID         11968
Image_name    36216
X             42143
filename      42143
md5           36212
file_url      36631
dtype: int64

23 CAMIDs lost, as expected from the error evaluation.

Did we lose any of our diversity? Taxonomic, image view, source (dataset or location of butterfly), etc. Only one stage is indicated in full master file.

In [8]:
stats_cols = ["Taxonomic_Name", "species", "subspecies", "genus", "Cross_Type", "View", "Locality", "Sex", "Dataset"]

master_checksums[stats_cols].nunique()

Taxonomic_Name    366
species           246
subspecies        155
genus              94
Cross_Type         30
View                7
Locality          644
Sex                 3
Dataset             7
dtype: int64

We lost one location and one dataset source to unsuccessful downloads.

#### Check on Lost Representation

In [12]:
master.loc[~master["Locality"].isin(list(master_checksums["Locality"].unique())), "Locality"].sample()

24204    Huaymayaco
Name: Locality, dtype: object

In [13]:
master.loc[~master["Dataset"].isin(list(master_checksums["Dataset"].unique())), "Dataset"].sample()

24233    Cambridge Collection
Name: Dataset, dtype: object

In [14]:
missing_samples = master.loc[(master["Locality"] == "Huaymayaco") | (master["Dataset"] == "Cambridge Collection")] 
missing_samples.info()

<class 'pandas.core.frame.DataFrame'>
Index: 47 entries, 24194 to 24240
Data columns (total 29 columns):
 #   Column            Non-Null Count  Dtype 
---  ------            --------------  ----- 
 0   CAMID             47 non-null     object
 1   X                 47 non-null     int64 
 2   Image_name        47 non-null     object
 3   View              47 non-null     object
 4   zenodo_name       47 non-null     object
 5   zenodo_link       47 non-null     object
 6   Sequence          47 non-null     object
 7   Taxonomic_Name    47 non-null     object
 8   Locality          47 non-null     object
 9   Sample_accession  0 non-null      object
 10  Collected_by      0 non-null      object
 11  Other_ID          0 non-null      object
 12  Date              47 non-null     object
 13  Dataset           47 non-null     object
 14  Store             0 non-null      object
 15  Brood             0 non-null      object
 16  Death_Date        47 non-null     object
 17  Cross_Type      

In [15]:
missing_samples.record_number.value_counts()

record_number
4289223    47
Name: count, dtype: int64

This record ([4289223](https://zenodo.org/records/4289223)) was examined in `EDA-DL-0-2.ipynb`. The images were listed in the provided metadata file for that record, but they did not appear in the record itself.
They are the majority of the images from Rachel Blow's Ecuador collection 2018 melpomene and timareta, near ikiam (taken in October 2019), listed in [0.2.rachel.blow.mel.tim.ikiam.csv](https://zenodo.org/records/4289223/preview/0.2.rachel.blow.mel.tim.ikiam.csv?include_deleted=0).

### Explore Downloaded Images

We have approximately 6000 duplicated images. We need to explore the information associated with each and reduce down to just unique images.

In [ ]:
# Are CAMIDs consistent in naming that duplicate images share CAMID (in same format)?

In [16]:
master_checksums["duplicate_md5"] = master_checksums.duplicated("md5", keep = False)
duplicated_images = master_checksums.loc[master_checksums["duplicate_md5"]]

print(duplicated_images.shape)
duplicated_images.nunique()

(11858, 32)


CAMID                2815
X                   11858
Image_name           5931
View                    2
zenodo_name            15
zenodo_link            15
Sequence             2815
Taxonomic_Name        195
Locality              210
Sample_accession      446
Collected_by            0
Other_ID              106
Date                  200
Dataset                 1
Store                  58
Brood                   9
Death_Date              0
Cross_Type              0
Stage                   0
Sex                     3
Unit_Type               3
file_type               3
record_number          15
species               121
subspecies             93
genus                  38
file_url             6346
hybrid_stat             2
filename            11858
filepath            11858
md5                  5927
duplicate_md5           1
dtype: int64

Observations:
- Half of the Zenodo records wind up with duplicated images. 
- `Image_name` uniqueness is close to `md5`, but there are 4 more unique image names than unique images. 
- None of the cross types are duplicated.
- We do have multiple unique images for a single `CAMID`, more than just dorsal vs ventral since there are 2815 unique CAMIDs and 5927 unique `md5` values (5927 = 2x2815 + 297)

In [22]:
# Save master file of all downloaded images with MD5s (no duplicate marker)
master_checksums[list(master_checksums.columns)[:-1]].to_csv("../metadata/deduplication/Jiggins_Zenodo_Img_Master_3477891Patch_downloaded.csv", index = False)

In [20]:
master_checksums.loc[~master_checksums["duplicate_md5"], "CAMID"].nunique()

9212

In [17]:
non_null_cols = [col for col in list(duplicated_images.columns) if duplicated_images.loc[duplicated_images[col].notna()].shape[0] > 0]
non_null_cols

['CAMID',
 'X',
 'Image_name',
 'View',
 'zenodo_name',
 'zenodo_link',
 'Sequence',
 'Taxonomic_Name',
 'Locality',
 'Sample_accession',
 'Other_ID',
 'Date',
 'Dataset',
 'Store',
 'Brood',
 'Sex',
 'Unit_Type',
 'file_type',
 'record_number',
 'species',
 'subspecies',
 'genus',
 'file_url',
 'hybrid_stat',
 'filename',
 'filepath',
 'md5',
 'duplicate_md5']

Let's remove all the columns with null values for easier analysis.

In [18]:
duplicated_images = duplicated_images[non_null_cols]
duplicated_images.info(show_counts=True)

<class 'pandas.core.frame.DataFrame'>
Index: 11858 entries, 3233 to 40186
Data columns (total 28 columns):
 #   Column            Non-Null Count  Dtype 
---  ------            --------------  ----- 
 0   CAMID             11858 non-null  object
 1   X                 11858 non-null  int64 
 2   Image_name        11858 non-null  object
 3   View              11858 non-null  object
 4   zenodo_name       11858 non-null  object
 5   zenodo_link       11858 non-null  object
 6   Sequence          11858 non-null  object
 7   Taxonomic_Name    11858 non-null  object
 8   Locality          11836 non-null  object
 9   Sample_accession  1846 non-null   object
 10  Other_ID          830 non-null    object
 11  Date              10046 non-null  object
 12  Dataset           11614 non-null  object
 13  Store             11670 non-null  object
 14  Brood             808 non-null    object
 15  Sex               11474 non-null  object
 16  Unit_Type         11614 non-null  object
 17  file_type     

There is some inconsistency with label coverage, which is hopefully resolvable for duplciated images.

In [23]:
duplicated_images.record_number.value_counts()

record_number
3477891    5501
2707828    1276
2714333    1113
2686762     980
2684906     747
2677821     703
2813153     435
4291095     415
2702457     260
2682458     148
2682669      92
2552371      91
2550097      50
2553977      27
5526257      20
Name: count, dtype: int64

This is mostly record 3477891 and the number of duplicate images in record 3477891 (5501) matches with the number of images that were matched to the multimedia CSV from that record to do the download patch. If I remove all instances of record 3477891, will we still have duplicates and will we have the same number of unique images?

### Check without Record 3477891

In [28]:
no_patch = master_checksums.loc[master_checksums["record_number"] != 3477891]

print(no_patch.shape[0])
no_patch[id_cols].nunique()

36642


CAMID         11968
Image_name    36216
X             36642
filename      36642
md5           36212
file_url      36631
dtype: int64

Yes, removing that record gives us the same number of unique images. ID Stats are consistent (unique MD5s and CAMIDs).

We have 430 images that are duplicates (`X - md5`).

Would keeping it allow us to remove others?

In [38]:
rec_3477891_urls = list(master_checksums.loc[master_checksums["record_number"] == 3477891, "file_url"].unique())

rec_3477891_images = master_checksums.loc[master_checksums["file_url"].isin(rec_3477891_urls)]

rec_3477891_images[id_cols].nunique()

CAMID          2704
Image_name     5497
X             10998
filename      10998
md5            5497
file_url       5497
dtype: int64

In [40]:
rec_3477891_images.record_number.value_counts()

record_number
3477891    5501
2707828    1276
2714333    1113
2686762     980
2684906     747
2677821     703
2702457     260
2682458     148
2682669      92
2552371      89
2550097      50
2813153      20
2553977      19
Name: count, dtype: int64

In [41]:
for record in list(rec_3477891_images.record_number.unique()):
    print(record)
    temp = master_checksums.loc[master_checksums["record_number"] == record]
    print(temp[["X","CAMID", "md5", "file_url"]].nunique())
    print()

2677821
X           769
CAMID       387
md5         769
file_url    769
dtype: int64

3477891
X           5501
CAMID       2704
md5         5497
file_url    5497
dtype: int64

2682458
X           950
CAMID       476
md5         950
file_url    950
dtype: int64

2682669
X           915
CAMID       458
md5         915
file_url    915
dtype: int64

2684906
X           977
CAMID       492
md5         977
file_url    977
dtype: int64

2552371
X           2392
CAMID       1189
md5         2391
file_url    2392
dtype: int64

2553977
X           158
CAMID        79
md5         154
file_url    157
dtype: int64

2686762
X           1384
CAMID        694
md5         1384
file_url    1384
dtype: int64

2550097
X           1400
CAMID        351
md5         1400
file_url    1400
dtype: int64

2702457
X           771
CAMID       388
md5         771
file_url    771
dtype: int64

2813153
X           523
CAMID       158
md5         523
file_url    523
dtype: int64

2707828
X           1292
CAMID        

Definitely cleaner to just remove record 3477891.

In [36]:
for record in list(no_patch.record_number.unique()):
    print(record)
    temp = no_patch.loc[no_patch["record_number"] == record]
    print(temp[["X","CAMID", "md5", "file_url"]].nunique())
    print()

4289223
X           145
CAMID        73
md5         145
file_url    145
dtype: int64

4288311
X           3088
CAMID       1050
md5         3088
file_url    3088
dtype: int64

2677821
X           769
CAMID       387
md5         769
file_url    769
dtype: int64

2682458
X           950
CAMID       476
md5         950
file_url    950
dtype: int64

2682669
X           915
CAMID       458
md5         915
file_url    915
dtype: int64

2684906
X           977
CAMID       492
md5         977
file_url    977
dtype: int64

2552371
X           2392
CAMID       1189
md5         2391
file_url    2392
dtype: int64

2553977
X           158
CAMID        79
md5         154
file_url    157
dtype: int64

2686762
X           1384
CAMID        694
md5         1384
file_url    1384
dtype: int64

2549524
X           1471
CAMID        368
md5         1471
file_url    1471
dtype: int64

2550097
X           1400
CAMID        351
md5         1400
file_url    1400
dtype: int64

4153502
X           583
CAMID     

Two records have a few duplicate images within them (record 2552371 has 1 and record 2553977 has 3).

In [29]:
no_patch["duplicate_md5"] = no_patch.duplicated("md5", keep = False)
no_patch["duplicate_md5"].value_counts()

/var/folders/nv/f0fq1p1n1_3b11x579py_0q80000gq/T/ipykernel_74270/343859278.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  no_patch["duplicate_md5"] = no_patch.duplicated("md5", keep = False)


duplicate_md5
False    35782
True       860
Name: count, dtype: int64

Yes, we still have duplicates.

In [46]:
non_dupes = no_patch.loc[~no_patch["duplicate_md5"]]
non_dupes[id_cols].nunique()

CAMID         11864
Image_name    35782
X             35782
filename      35782
md5           35782
file_url      35782
dtype: int64

In [47]:
non_dupes.View.value_counts()

View
dorsal                17019
ventral               16954
hindwing dorsal         254
hindwing ventral        254
forewing dorsal         252
forewing ventral        252
dorsal and ventral       18
Name: count, dtype: int64

In [48]:
non_dupes.file_type.value_counts()

file_type
jpg    25618
raw    10111
tif       53
Name: count, dtype: int64

In [50]:
non_dupes.loc[non_dupes["file_type"] != "raw", "View"].value_counts()

View
dorsal                12405
ventral               12342
hindwing dorsal         127
hindwing ventral        127
forewing dorsal         126
forewing ventral        126
dorsal and ventral       18
Name: count, dtype: int64

So among our non-duplicated images we do see multiple images of the same specimen after accounting for file type and view of the specimen (as determined by the number of ventral or dorsal images).

### Explore the duplicates
Ensure that we maintain all the available metadata associated with the images as we remove duplicates.

In [30]:
no_patch_duplicates = no_patch.loc[no_patch["duplicate_md5"]]

no_patch_duplicates[non_null_cols].info()

<class 'pandas.core.frame.DataFrame'>
Index: 860 entries, 11978 to 40145
Data columns (total 28 columns):
 #   Column            Non-Null Count  Dtype 
---  ------            --------------  ----- 
 0   CAMID             860 non-null    object
 1   X                 860 non-null    int64 
 2   Image_name        860 non-null    object
 3   View              860 non-null    object
 4   zenodo_name       860 non-null    object
 5   zenodo_link       860 non-null    object
 6   Sequence          860 non-null    object
 7   Taxonomic_Name    860 non-null    object
 8   Locality          838 non-null    object
 9   Sample_accession  0 non-null      object
 10  Other_ID          806 non-null    object
 11  Date              0 non-null      object
 12  Dataset           616 non-null    object
 13  Store             832 non-null    object
 14  Brood             800 non-null    object
 15  Sex               608 non-null    object
 16  Unit_Type         616 non-null    object
 17  file_type      

A couple more nulls were introduced.

In [31]:
no_patch_duplicates[id_cols].nunique()

CAMID         111
Image_name    434
X             860
filename      860
md5           430
file_url      849
dtype: int64

In [32]:
no_patch_duplicates[stats_cols].nunique()

Taxonomic_Name    4
species           3
subspecies        3
genus             1
Cross_Type        0
View              2
Locality          6
Sex               2
Dataset           1
dtype: int64

In [33]:
no_patch_duplicates.record_number.value_counts()

record_number
4291095    415
2813153    415
5526257     20
2553977      8
2552371      2
Name: count, dtype: int64

Looks like we just have two of each image.

I'd hazard a guess that records [4291095](https://zenodo.org/records/4291095) and [2813153](https://zenodo.org/records/2813153) are duplicates of each other and contain some of the images from the others (as there are 430 unique images).

based on their descriptions (on Zenodo) it doesn't seem like they should have any overlap...

In [34]:
no_patch_duplicates.loc[no_patch_duplicates["record_number"] == 4291095].head(10)

CAMID      X       Image_name     View           zenodo_name  \
32499  CAM041807  40194  CAM041807_d.CR2   dorsal  0.gmk.broods.all.csv   
32502  CAM041807  40197  CAM041807_v.JPG  ventral  0.gmk.broods.all.csv   
32504  CAM041807  40195  CAM041807_d.JPG   dorsal  0.gmk.broods.all.csv   
32505  CAM041807  40196  CAM041807_v.CR2  ventral  0.gmk.broods.all.csv   
32507  CAM041808  40198  CAM041808_d.CR2   dorsal  0.gmk.broods.all.csv   
32511  CAM041808  40201  CAM041808_v.JPG  ventral  0.gmk.broods.all.csv   
32512  CAM041808  40199  CAM041808_d.JPG   dorsal  0.gmk.broods.all.csv   
32513  CAM041808  40200  CAM041808_v.CR2  ventral  0.gmk.broods.all.csv   
32517  CAM041809  40203  CAM041809_d.JPG   dorsal  0.gmk.broods.all.csv   
32518  CAM041809  40205  CAM041809_v.JPG  ventral  0.gmk.broods.all.csv   

                             zenodo_link Sequence  \
32499  https://zenodo.org/record/4291095   41,807   
32502  https://zenodo.org/record/4291095   41,807   
32504  https://zenodo.org/record/4291095   41,807   
32505  https://zenodo.org/record/4291095   41,807   
32507  https://zenodo.org/record/4291095   41,808   
32511  https://zenodo.org/record/4291095   41,808   
32512  https://zenodo.org/record/4291095   41,808   
32513  https://zenodo.org/record/4291095   41,808   
32517  https://zenodo.org/record/4291095   41,809   
32518  https://zenodo.org/record/4291095   41,809   

                        Taxonomic_Name           Locality Sample_accession  \
32499  Heliconius erato ssp. lativitta  Ikiam Mariposario              NaN   
32502  Heliconius erato ssp. lativitta  Ikiam Mariposario              NaN   
32504  Heliconius erato ssp. lativitta  Ikiam Mariposario              NaN   
32505  Heliconius erato ssp. lativitta  Ikiam Mariposario              NaN   
32507  Heliconius erato ssp. lativitta  Ikiam Mariposario              NaN   
32511  Heliconius erato ssp. lativitta  Ikiam Mariposario              NaN   
32512  Heliconius erato ssp. lativitta  Ikiam Mariposario              NaN   
32513  Heliconius erato ssp. lativitta  Ikiam Mariposario              NaN   
32517  Heliconius erato ssp. lativitta  Ikiam Mariposario              NaN   
32518  Heliconius erato ssp. lativitta  Ikiam Mariposario              NaN   

       ... record_number           species subspecies       genus  \
32499  ...       4291095  Heliconius erato  lativitta  Heliconius   
32502  ...       4291095  Heliconius erato  lativitta  Heliconius   
32504  ...       4291095  Heliconius erato  lativitta  Heliconius   
32505  ...       4291095  Heliconius erato  lativitta  Heliconius   
32507  ...       4291095  Heliconius erato  lativitta  Heliconius   
32511  ...       4291095  Heliconius erato  lativitta  Heliconius   
32512  ...       4291095  Heliconius erato  lativitta  Heliconius   
32513  ...       4291095  Heliconius erato  lativitta  Heliconius   
32517  ...       4291095  Heliconius erato  lativitta  Heliconius   
32518  ...       4291095  Heliconius erato  lativitta  Heliconius   

                                                file_url hybrid_stat  \
32499  https://zenodo.org/record/4291095/files/CAM041...  non-hybrid   
32502  https://zenodo.org/record/4291095/files/CAM041...  non-hybrid   
32504  https://zenodo.org/record/4291095/files/CAM041...  non-hybrid   
32505  https://zenodo.org/record/4291095/files/CAM041...  non-hybrid   
32507  https://zenodo.org/record/4291095/files/CAM041...  non-hybrid   
32511  https://zenodo.org/record/4291095/files/CAM041...  non-hybrid   
32512  https://zenodo.org/record/4291095/files/CAM041...  non-hybrid   
32513  https://zenodo.org/record/4291095/files/CAM041...  non-hybrid   
32517  https://zenodo.org/record/4291095/files/CAM041...  non-hybrid   
32518  https://zenodo.org/record/4291095/files/CAM041...  non-hybrid   

                    filename  \
32499  40194_CAM041807_d.CR2   
32502  40197_CAM041807_v.JPG   
32504  40195_CAM041807_d.JPG   
32505  40196_CAM041807_v.CR2   
32507  40198_CAM041808_d.CR2 

In [35]:
rec_4291095 = no_patch_duplicates.loc[no_patch_duplicates["record_number"] == 4291095]
rec_4291095["dupes"] = rec_4291095.duplicated("md5")
rec_4291095["dupes"].value_counts()

/var/folders/nv/f0fq1p1n1_3b11x579py_0q80000gq/T/ipykernel_74270/3053018095.py:2: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  rec_4291095["dupes"] = rec_4291095.duplicated("md5")


dupes
False    415
Name: count, dtype: int64

In [42]:
no_patch_duplicates.loc[no_patch_duplicates["record_number"].isin([4291095, 2813153]), "md5"].nunique()

415

These shouldn't be duplicates based on their Zenodo descriptions. Let's download their CSV files and check the metadata matches.

In [43]:
df_4291095 = pd.read_csv("../metadata/deduplication/Zenodo_meta_files/0.gmk.broods.all_(rec4291095).csv", low_memory=False)
df_2813153 = pd.read_csv("../metadata/deduplication/Zenodo_meta_files/CAM.coll.images.batch10_(rec2813153).csv", low_memory=False)

In [44]:
df_4291095.shape[0], df_2813153.shape[0]

(2220, 591)

In [45]:
master_checksums.loc[master_checksums["record_number"].isin([4291095, 2813153]), "record_number"].value_counts()

record_number
4291095    2212
2813153     523
Name: count, dtype: int64

In [52]:
df_4291095.columns

Index(['image.name', 'unit.id', 'side'], dtype='object')

In [94]:
rec_4291095_check = pd.merge(master_checksums.loc[master_checksums["record_number"] == 4291095],
                             df_4291095,
                             left_on = "Image_name",
                             right_on = "image.name",
                             how = "inner")

rec_4291095_check.shape[0]

2212

In [54]:
df_2813153.columns

Index(['Filename', 'UnitID', 'View'], dtype='object')

In [55]:
rec_2813153_check = pd.merge(master_checksums.loc[master_checksums["record_number"] == 2813153],
                             df_2813153,
                             left_on = "Image_name",
                             right_on = "Filename",
                             how = "inner")

rec_2813153_check.shape[0]

523

These do both seem to align properly, are the `UnitID`/`unit.id` overlapping for 415 images?

In [62]:
rec_match = pd.merge(rec_4291095_check[["X", "Image_name", "CAMID", "unit.id", "md5", "Taxonomic_Name"]],
                    rec_2813153_check[["X", "Image_name", "CAMID", "UnitID", "md5", "Taxonomic_Name"]],
                    left_on = ["CAMID", "unit.id", "Taxonomic_Name", "md5"],
                    right_on = ["CAMID", "UnitID", "Taxonomic_Name", "md5"],
                    how = "inner")

print(rec_match.shape[0])
rec_match.nunique()

415


X_x               415
Image_name_x      415
CAMID             104
unit.id           104
md5               415
Taxonomic_Name      1
X_y               415
Image_name_y      415
UnitID            104
dtype: int64

In [63]:
rec_match.head()


X_x     Image_name_x      CAMID    unit.id  \
0  40194  CAM041807_d.CR2  CAM041807  CAM041807   
1  40197  CAM041807_v.JPG  CAM041807  CAM041807   
2  40195  CAM041807_d.JPG  CAM041807  CAM041807   
3  40196  CAM041807_v.CR2  CAM041807  CAM041807   
4  40198  CAM041808_d.CR2  CAM041808  CAM041808   

                                md5                   Taxonomic_Name    X_y  \
0  1ef3dbe7b286a34882d21ef39424f18a  Heliconius erato ssp. lativitta  14461   
1  844f9b09adda5d919694a8c1a38ca991  Heliconius erato ssp. lativitta  14464   
2  1e77684537bc187b8e82b0f9f4342275  Heliconius erato ssp. lativitta  14462   
3  b1daeb529e16952906c986d193bcc32d  Heliconius erato ssp. lativitta  14463   
4  e1b16f08005517abfda5ef098b11b8b1  Heliconius erato ssp. lativitta  14465   

      Image_name_y     UnitID  
0  CAM041807_d.CR2  CAM041807  
1  CAM041807_v.JPG  CAM041807  
2  CAM041807_d.JPG  CAM041807  
3  CAM041807_v.CR2  CAM041807  
4  CAM041808_d.CR2  CAM041808

The big question in removing duplicate records is just if all the metadata assoicated to the image remains the same. This would be all metadata other than `record_number`, `file_url`, `X`, `zenodo_link`, `zenodo_name` (CSV source), `Dataset` (Zenodo record name), `Image_name`, and possibly some other columns we don't usually work with.

In [71]:
diff_cols = ["record_number", "file_url", "X", "zenodo_link", "zenodo_name", "filename", "filepath", "Image_name", "Dataset"]

merge_cols = [col for col in list(no_patch_duplicates.columns)[:-1] if (no_patch_duplicates.loc[no_patch_duplicates[col].notna()].shape[0] > 0) and (col not in diff_cols)]
merge_cols

['CAMID',
 'View',
 'Sequence',
 'Taxonomic_Name',
 'Locality',
 'Other_ID',
 'Store',
 'Brood',
 'Sex',
 'Unit_Type',
 'file_type',
 'species',
 'subspecies',
 'genus',
 'hybrid_stat',
 'md5']

Start with these two larger overlaps

In [95]:
rec_2813153 = no_patch_duplicates.loc[no_patch_duplicates["record_number"] == 2813153]
rec_2813153.shape

(415, 32)

In [96]:
merge_check = pd.merge(rec_4291095,
                       rec_2813153,
                       on = merge_cols,
                       how = "inner")

merge_check.shape[0]

311

In [111]:
overlap_non_null_cols = [col for col in list(no_patch_duplicates.columns)[:-1] if (no_patch_duplicates.loc[no_patch_duplicates[col].notna()].shape[0] > 0)]
overlap_non_null_cols

['CAMID',
 'X',
 'Image_name',
 'View',
 'zenodo_name',
 'zenodo_link',
 'Sequence',
 'Taxonomic_Name',
 'Locality',
 'Other_ID',
 'Dataset',
 'Store',
 'Brood',
 'Sex',
 'Unit_Type',
 'file_type',
 'record_number',
 'species',
 'subspecies',
 'genus',
 'file_url',
 'hybrid_stat',
 'filename',
 'filepath',
 'md5']

In [113]:
for col in overlap_non_null_cols:
    merge_on = ["md5", col]
    temp = pd.merge(rec_2813153,
                    rec_4291095,
                    on = merge_on,
                    how = "inner")
    print(col, temp.shape[0])
    

CAMID 415
X 0
Image_name 415
View 311
zenodo_name 0
zenodo_link 0
Sequence 415
Taxonomic_Name 415
Locality 415
Other_ID 415
Dataset 415
Store 415
Brood 415
Sex 415
Unit_Type 415
file_type 415
record_number 0
species 415
subspecies 415
genus 415
file_url 0
hybrid_stat 415
filename 0
filepath 0
md5 415


Expected columns fail, but also `View` seems to be an issue, so let's look at where the view disagrees. Note that the `Image_name` seems to match for all of them, this could be an option for checking proper views.

In [130]:
view_check_cols = ["X", "Image_name", "CAMID", "md5", "Taxonomic_Name", "View", "file_type"]
view_check = pd.merge(rec_2813153[view_check_cols],
                      rec_4291095[view_check_cols],
                      on = ["Image_name", "CAMID", "md5", "Taxonomic_Name", "file_type"],
                      suffixes = ("_28", "_42"),
                      how = "inner")

view_check.shape

(415, 9)

In [131]:
view_check["mismatched_view"] = view_check["View_28"] != view_check["View_42"]
view_check["mismatched_view"].value_counts()

mismatched_view
False    311
True     104
Name: count, dtype: int64

In [132]:
view_check.loc[view_check["mismatched_view"]].sample(10)

X_28       Image_name      CAMID                               md5  \
136  14599  CAM041841_v.CR2  CAM041841  005a48b915e7c5a750648e5f37ea5fd8   
118  14579  CAM041836_v.CR2  CAM041836  6c816d18dc8c903fbdbfb93f4c04c3b0   
148  14611  CAM041844_v.CR2  CAM041844  59e2410288a9636c691086cc3720c761   
56   14519  CAM041821_v.CR2  CAM041821  57163f6da6697359d233a6e712373b7d   
281  14743  CAM041878_v.CR2  CAM041878  171701048825a19051127dc253e39e50   
86   14547  CAM041828_v.CR2  CAM041828  c6de0b670edbe46881497bf60b1f9853   
194  14655  CAM041856_v.CR2  CAM041856  6f5face02339ba69483f6dbf6c0aa601   
18   14479  CAM041811_v.CR2  CAM041811  9cb25be5951488b9e37342586cb678f6   
290  14751  CAM041880_v.CR2  CAM041880  b27fa3842baba1f3bb1679419dd009e7   
310  14771  CAM041885_v.CR2  CAM041885  d7105469b2c4b24fb288e7e3b9b1241d   

                      Taxonomic_Name View_28 file_type   X_42  View_42  \
136  Heliconius erato ssp. lativitta  dorsal       raw  40332  ventral   
118  Heliconius erato ssp. lativitta  dorsal       raw  40312  ventral   
148  Heliconius erato ssp. lativitta  dorsal       raw  40344  ventral   
56   Heliconius erato ssp. lativitta  dorsal       raw  40252  ventral   
281  Heliconius erato ssp. lativitta  dorsal       raw  40477  ventral   
86   Heliconius erato ssp. lativitta  dorsal       raw  40280  ventral   
194  Heliconius erato ssp. lativitta  dorsal       raw  40389  ventral   
18   Heliconius erato ssp. lativitta  dorsal       raw  40212  ventral   
290  Heliconius erato ssp. lativitta  dorsal       raw  40485  ventral   
310  Heliconius erato ssp. lativitta  dorsal       raw  40505  ventral   

     mismatched_view  
136             True  
118             True  
148             True  
56              True  
281             True  
86              True  
194             True  
18              True  
290             True  
310             True

In [133]:
view_check.loc[view_check["mismatched_view"], "file_type"].value_counts()

file_type
raw    104
Name: count, dtype: int64

Ahh only the raw photos have the mismatch. Were they the only ones mislabeled or were their associated JPGs mislabeled?

In [134]:
mismatched_view_cams = list(view_check.loc[view_check["mismatched_view"], "CAMID"].unique())
view_check.loc[(view_check["CAMID"].isin(mismatched_view_cams)) & (view_check["file_type"] == "jpg")].sample(10)

X_28       Image_name      CAMID                               md5  \
276  14738  CAM041877_d.JPG  CAM041877  7cba96d6031a6c4b8ccdb9971a5f9728   
121  14582  CAM041837_d.JPG  CAM041837  a7cc8d0b392b2088e122b736e8a09650   
346  14810  CAM041895_d.JPG  CAM041895  60d3c82b6c57c08e3c71b73982aa1f09   
278  14740  CAM041877_v.JPG  CAM041877  46eaec54590b045ab352728a4b12441a   
180  14644  CAM041852_v.JPG  CAM041852  40b5d568cf0ab0590756181307dbf3df   
176  14638  CAM041851_d.JPG  CAM041851  6e0ef053a5208fb33fe612777e85fe90   
103  14564  CAM041832_v.JPG  CAM041832  a0f4b27b90a322c36c26d8375f303adb   
74   14534  CAM041825_d.JPG  CAM041825  795185b9e27ff897d94278a11eec5c99   
186  14646  CAM041853_d.JPG  CAM041853  9f3ad95d8ff999ac4b8bb76cad171aaf   
283  14742  CAM041878_d.JPG  CAM041878  c0d154ebbf7552bcdbcb233556a5f286   

                      Taxonomic_Name  View_28 file_type   X_42  View_42  \
276  Heliconius erato ssp. lativitta   dorsal       jpg  40472   dorsal   
121  Heliconius erato ssp. lativitta   dorsal       jpg  40315   dorsal   
346  Heliconius erato ssp. lativitta   dorsal       jpg  40544   dorsal   
278  Heliconius erato ssp. lativitta  ventral       jpg  40474  ventral   
180  Heliconius erato ssp. lativitta  ventral       jpg  40377  ventral   
176  Heliconius erato ssp. lativitta   dorsal       jpg  40371   dorsal   
103  Heliconius erato ssp. lativitta  ventral       jpg  40297  ventral   
74   Heliconius erato ssp. lativitta   dorsal       jpg  40267   dorsal   
186  Heliconius erato ssp. lativitta   dorsal       jpg  40379   dorsal   
283  Heliconius erato ssp. lativitta   dorsal       jpg  40476   dorsal   

     mismatched_view  
276            False  
121            False  
346            False  
278            False  
180            False  
176            False  
103            False  
74             False  
186            False  
283            False

OK, it _seems_ that it was just the raw photos that were mislabeled. We'll keep those updates.

From this sample, it looks like record 42 fixed some mislabels from record 28. Should probably check if record 3477891 fixed mislabeling from the earlier records that it duplicated.

### Check Record 3477891 Duplicates

In [119]:
md5s_3477891 = list(master_checksums.loc[master_checksums["record_number"] == 3477891, "md5"].unique())
patch_dupes = master_checksums.loc[master_checksums["md5"].isin(md5s_3477891)]
patch_dupes[id_cols].nunique()

CAMID          2704
Image_name     5497
X             10998
filename      10998
md5            5497
file_url       5497
dtype: int64

In [120]:
patch_df = patch_dupes.loc[patch_dupes["record_number"] == 3477891]
patch_matches = patch_dupes.loc[patch_dupes["record_number"] != 3477891]

In [121]:
patch_non_null_cols = [col for col in list(patch_dupes.columns)[:-1] if (patch_dupes.loc[patch_dupes[col].notna()].shape[0] > 0)]
for col in patch_non_null_cols:
    merge_on = ["md5", col]
    temp = pd.merge(patch_df,
                    patch_matches,
                    on = merge_on,
                    how = "inner")
    print(col, temp.shape[0])
    

CAMID 5501
X 0
Image_name 5501
View 5495
zenodo_name 0
zenodo_link 0
Sequence 5501
Taxonomic_Name 5501
Locality 5501
Sample_accession 5501
Other_ID 5501
Date 5501
Dataset 5501
Store 5501
Brood 5501
Sex 5501
Unit_Type 5501
file_type 5501
record_number 0
species 5501
subspecies 5501
genus 5501
file_url 5501
hybrid_stat 5501
filename 0
filepath 0
md5 5501


We again have the only inconsistency in the `View` column, where they do not align exactly (though it's only 6 differences).

In [122]:
patch_view_check = pd.merge(patch_matches[view_check_cols],
                      patch_df[view_check_cols],
                      on = ["Image_name", "CAMID", "md5", "Taxonomic_Name"],
                      suffixes = ("_old", "_patch"),
                      how = "inner")

print(patch_view_check.shape)

patch_view_check["mismatched_view"] = patch_view_check["View_old"] != patch_view_check["View_patch"]
patch_view_check["mismatched_view"].value_counts()

(5501, 8)


mismatched_view
False    5495
True        6
Name: count, dtype: int64

In [123]:
patch_view_check.loc[patch_view_check["mismatched_view"]]

X_old                       Image_name      CAMID  \
1689  26075                     DSC_0697.jpg  CAM008523   
1871  26059                     8624-UND.jpg  CAM008624   
1880  26061                     8628-UND.jpg  CAM008628   
1886  26063                     8631-UND.jpg  CAM008631   
2516  26066  9117_H_m_ecuadorensis_V.JPG.jpg  CAM009117   
2531  26068  9121_H_m_ecuadorensis_V.JPG.jpg  CAM009121   

                                   md5  \
1689  764c722faeefa48aed09aef1956738a8   
1871  4a3b6c97a131436f3e5f95b0ef7695d2   
1880  97fdfb3de2e4a34f1c243056348962c5   
1886  e1c82f4e814c7a6c56ebc34b0f502298   
2516  66a8b638d961955d3cd168c3168667ed   
2531  a14ff471e6be6c26bc2c0d8409a7a1e0   

                              Taxonomic_Name View_old  X_patch View_patch  \
1689       Heliconius timareta ssp. timareta  ventral    49955     dorsal   
1871      Heliconius timareta ssp. thelxinoe  ventral    44341     dorsal   
1880      Heliconius timareta ssp. thelxinoe  ventral    44342     dorsal   
1886      Heliconius timareta ssp. thelxinoe  ventral    44343     dorsal   
2516  Heliconius melpomene ssp. ecuadorensis  ventral    44375     dorsal   
2531  Heliconius melpomene ssp. ecuadorensis  ventral    44379     dorsal   

      mismatched_view  
1689             True  
1871             True  
1880             True  
1886             True  
2516             True  
2531             True

In [128]:
patch_view_check["md5_dupe"] = patch_view_check.duplicated("md5", keep = False)
patch_view_check.loc[patch_view_check["md5_dupe"]]

X_old                       Image_name      CAMID  \
2516  26066  9117_H_m_ecuadorensis_V.JPG.jpg  CAM009117   
2517  26066  9117_H_m_ecuadorensis_V.JPG.jpg  CAM009117   
2519  26065  9117_H_m_ecuadorensis_D.JPG.jpg  CAM009117   
2520  26065  9117_H_m_ecuadorensis_D.JPG.jpg  CAM009117   
2529  26067  9121_H_m_ecuadorensis_D.JPG.jpg  CAM009121   
2530  26067  9121_H_m_ecuadorensis_D.JPG.jpg  CAM009121   
2531  26068  9121_H_m_ecuadorensis_V.JPG.jpg  CAM009121   
2532  26068  9121_H_m_ecuadorensis_V.JPG.jpg  CAM009121   

                                   md5  \
2516  66a8b638d961955d3cd168c3168667ed   
2517  66a8b638d961955d3cd168c3168667ed   
2519  d10fcc5232e4c994d32e8181cb6e71e1   
2520  d10fcc5232e4c994d32e8181cb6e71e1   
2529  d53b79f77d12e7da1eb2ddf17418de9c   
2530  d53b79f77d12e7da1eb2ddf17418de9c   
2531  a14ff471e6be6c26bc2c0d8409a7a1e0   
2532  a14ff471e6be6c26bc2c0d8409a7a1e0   

                              Taxonomic_Name View_old  X_patch View_patch  \
2516  Heliconius melpomene ssp. ecuadorensis  ventral    44375     dorsal   
2517  Heliconius melpomene ssp. ecuadorensis  ventral    44374    ventral   
2519  Heliconius melpomene ssp. ecuadorensis   dorsal    44372     dorsal   
2520  Heliconius melpomene ssp. ecuadorensis   dorsal    44373     dorsal   
2529  Heliconius melpomene ssp. ecuadorensis   dorsal    44376     dorsal   
2530  Heliconius melpomene ssp. ecuadorensis   dorsal    44377     dorsal   
2531  Heliconius melpomene ssp. ecuadorensis  ventral    44379     dorsal   
2532  Heliconius melpomene ssp. ecuadorensis  ventral    44378    ventral   

      mismatched_view  md5_dupe  
2516             True      True  
2517            False      True  
2519            False      True  
2520            False      True  
2529            False      True  
2530            False      True  
2531             True      True  
2532            False      True

Manual check and confirmation with Christopher suggests that the additions (and duplications) were mislabled, so we will be proceeding without the patch.

### Check the final Non-patch duplicates
Those not in records `4291095, 2813153`:
```
5526257     20
2553977      8
2552371      2
```

In [135]:
small_overlap = no_patch_duplicates.loc[~no_patch_duplicates["record_number"].isin([4291095, 2813153])]
small_overlap.md5.nunique()

15

In [137]:
#check smallest two for overlap
small_overlap.loc[small_overlap["record_number"].isin([2553977, 2552371])]

CAMID      X                               Image_name     View  \
11978  CAM010354  23471                               10354d.jpg   dorsal   
12010  CAM010362  23484                               10362v.jpg  ventral   
40112  CAM050036  26102      CAM050036_S1_9_FW_IMG_8547_wb_2.tif   dorsal   
40113  CAM050036  26105   CAM050036_S1_9_HW_wt_IMG_8541_cut3.tif   dorsal   
40116  CAM050036  26115     CAM050036_S1_9_FW_IMG_8547_cut_2.tif   dorsal   
40120  CAM050036  26116  CAM050036_S1_9_HW_wt_IMG_8541_cut_3.tif   dorsal   
40138  CAM050147  26112             CAM050147_DS1_IMG_8513_4.tif   dorsal   
40141  CAM050147  26197      CAM050147_DS1_HW_IMG_8537_cut_3.tif   dorsal   
40144  CAM050147  26196      CAM050147_DS1_HW_IMG_8537_cut_3.tif   dorsal   
40145  CAM050147  26117      CAM050147_DS1_FW_IMG_8513_cut_4.tif   dorsal   

                                          zenodo_name  \
11978  Heliconius_wing_old_photos_2001_2019_part1.csv   
12010  Heliconius_wing_old_photos_2001_2019_part1.csv   
40112  Heliconius_wing_old_photos_2001_2019_part3.csv   
40113  Heliconius_wing_old_photos_2001_2019_part3.csv   
40116  Heliconius_wing_old_photos_2001_2019_part3.csv   
40120  Heliconius_wing_old_photos_2001_2019_part3.csv   
40138  Heliconius_wing_old_photos_2001_2019_part3.csv   
40141  Heliconius_wing_old_photos_2001_2019_part3.csv   
40144  Heliconius_wing_old_photos_2001_2019_part3.csv   
40145  Heliconius_wing_old_photos_2001_2019_part3.csv   

                             zenodo_link Sequence             Taxonomic_Name  \
11978  https://zenodo.org/record/2552371   10,354             Heliconius sp.   
12010  https://zenodo.org/record/2552371   10,362             Heliconius sp.   
40112  https://zenodo.org/record/2553977   50,036  Heliconius sara ssp. sara   
40113  https://zenodo.org/record/2553977   50,036  Heliconius sara ssp. sara   
40116  https://zenodo.org/record/2553977   50,036  Heliconius sara ssp. sara   
40120  https://zenodo.org/record/2553977   50,036  Heliconius sara ssp. sara   
40138  https://zenodo.org/record/2553977   50,147  Heliconius sara ssp. sara   
40141  https://zenodo.org/record/2553977   50,147  Heliconius sara ssp. sara   
40144  https://zenodo.org/record/2553977   50,147  Heliconius sara ssp. sara   
40145  https://zenodo.org/record/2553977   50,147  Heliconius sara ssp. sara   

                 Locality Sample_accession  ... record_number  \
11978                 NaN              NaN  ...       2552371   
12010                 NaN              NaN  ...       2552371   
40112  Gamboa_insectaries              NaN  ...       2553977   
40113  Gamboa_insectaries              NaN  ...       2553977   
40116  Gamboa_insectaries              NaN  ...       2553977   
40120  Gamboa_insectaries              NaN  ...       2553977   
40138           Madingley              NaN  ...       2553977   
40141           Madingley              NaN  ...       2553977   
40144           Madingley              NaN  ...       2553977   
40145           Madingley              NaN  ...       2553977   

               species subspecies       genus  \
11978   Heliconius sp.        NaN  Heliconius   
12010   Heliconius sp.        NaN  Heliconius   
40112  Heliconius sara       sara  Heliconius   
40113  Heliconius sara       sara  Heliconius   
40116  Heliconius sara       sara  Heliconius   
40120  Heliconius sara       sara  Heliconius   
40138  Heliconius sara       sara  Heliconius   
40141  Heliconius sara       sara  Heliconius   
40144  Heliconius sara       sara  Heliconius   
40145  Heliconius sara       sara  Heliconius   

                                                file_url hybrid_stat  \
11978  https://zenodo.org/record/2552371/files/10354d...         NaN   
12010  https://zenodo.org/record/2552371/files/10362v...         NaN   
40112  https://zenodo.org/record/2553977/files/CAM050...  non-hybrid   
40113  https://zenodo.org/record/2553977/files/CAM050...  non-hybrid   
40116  https://zenodo.org/record/25539

These do not seem to overlap. Instead, they seem to duplicate within each record.

Likely there is duplication introduced also in record 5526257.

In [139]:
rec_55 = small_overlap.loc[small_overlap["record_number"] == 5526257]
recs_255 = small_overlap.loc[small_overlap["record_number"].isin([2553977, 2552371])]

print("Record 5526257 uniqueness:", rec_55.md5.nunique())
print("Records 255.. uniqueness:", recs_255.md5.nunique())

Record 5526257 uniqueness: 10
Records 255.. uniqueness: 5


In [140]:
columns_55 = ["CAMID", "filename", "View", "Taxonomic_Name", "Locality", "md5"]

In [142]:
rec_55[columns_55].sort_values(by = "md5")

CAMID               filename     View  \
38765  CAM045009  42597_CAM045009_d.CR2   dorsal   
38764  CAM045009  42596_CAM045009_d.CR2   dorsal   
39189  CAM045114  43024_CAM045114_v.JPG  ventral   
39193  CAM045114  43025_CAM045114_v.JPG  ventral   
38755  CAM045006  42587_CAM045006_v.CR2  ventral   
38750  CAM045006  42586_CAM045006_v.CR2  ventral   
38770  CAM045009  42602_CAM045009_v.JPG  ventral   
38771  CAM045009  42603_CAM045009_v.JPG  ventral   
38754  CAM045006  42585_CAM045006_d.JPG   dorsal   
38753  CAM045006  42584_CAM045006_d.JPG   dorsal   
38752  CAM045006  42583_CAM045006_d.CR2   dorsal   
38751  CAM045006  42582_CAM045006_d.CR2   dorsal   
38766  CAM045009  42598_CAM045009_d.JPG   dorsal   
38767  CAM045009  42599_CAM045009_d.JPG   dorsal   
39192  CAM045114  43023_CAM045114_v.CR2  ventral   
39191  CAM045114  43022_CAM045114_v.CR2  ventral   
38768  CAM045009  42600_CAM045009_v.CR2  ventral   
38769  CAM045009  42601_CAM045009_v.CR2  ventral   
38756  CAM045006  42588_CAM045006_v.JPG  ventral   
38757  CAM045006  42589_CAM045006_v.JPG  ventral   

                     Taxonomic_Name Locality                               md5  
38765  Heliconius erato ssp. cyrbia      NaN  3aa4f36fe82bf582cdb09e22cf998ea0  
38764  Heliconius erato ssp. cyrbia      NaN  3aa4f36fe82bf582cdb09e22cf998ea0  
39189  Heliconius erato ssp. cyrbia      NaN  46264ce1e0e5bd93735534c8cdc3a9fb  
39193  Heliconius erato ssp. cyrbia      NaN  46264ce1e0e5bd93735534c8cdc3a9fb  
38755  Heliconius erato ssp. cyrbia      NaN  5c71b211545b1b469dfadb06b35ccd57  
38750  Heliconius erato ssp. cyrbia      NaN  5c71b211545b1b469dfadb06b35ccd57  
38770  Heliconius erato ssp. cyrbia      NaN  6e1c1b698bbafe5fe686c00f93991759  
38771  Heliconius erato ssp. cyrbia      NaN  6e1c1b698bbafe5fe686c00f93991759  
38754  Heliconius erato ssp. cyrbia      NaN  7f09b3de42a6771d0ac63bee6995bc49  
38753  Heliconius erato ssp. cyrbia      NaN  7f09b3de42a6771d0ac63bee6995bc49  
38752  Heliconius erato ssp. cyrbia      NaN  b146797ff261debef1f8ae93ce528817  
38751  Heliconius erato ssp. cyrbia      NaN  b146797ff261debef1f8ae93ce528817  
38766  Heliconius erato ssp. cyrbia      NaN  bd26f12f1fb204c623ff9fd615d6a0fd  
38767  Heliconius erato ssp. cyrbia      NaN  bd26f12f1fb204c623ff9fd615d6a0fd  
39192  Heliconius erato ssp. cyrbia      NaN  db4c1d373140cd4e56f0976a88b0ab54  
39191  Heliconius erato ssp. cyrbia      NaN  db4c1d373140cd4e56f0976a88b0ab54  
38768  Heliconius erato ssp. cyrbia      NaN  e9acf59ae9d96564f5cd8342281e4514  
38769  Heliconius erato ssp. cyrbia      NaN  e9acf59ae9d96564f5cd8342281e4514  
38756  Heliconius erato ssp. cyrbia      NaN  f64512f4ce131775f3594e96ba761fa9  
38757  Heliconius erato ssp. cyrbia      NaN  f64512f4ce131775f3594e96ba761fa9

These are all exact duplicates...

In [143]:
rec_55.duplicated(["CAMID", "Image_name", "View", "Taxonomic_Name", "Locality", "md5"], keep = "first").value_counts()

False    10
True     10
Name: count, dtype: int64

In [148]:
recs_255[columns_55].sort_values(by = "md5")

CAMID                                       filename     View  \
40141  CAM050147      26197_CAM050147_DS1_HW_IMG_8537_cut_3.tif   dorsal   
40144  CAM050147      26196_CAM050147_DS1_HW_IMG_8537_cut_3.tif   dorsal   
40112  CAM050036      26102_CAM050036_S1_9_FW_IMG_8547_wb_2.tif   dorsal   
40116  CAM050036     26115_CAM050036_S1_9_FW_IMG_8547_cut_2.tif   dorsal   
40138  CAM050147             26112_CAM050147_DS1_IMG_8513_4.tif   dorsal   
40145  CAM050147      26117_CAM050147_DS1_FW_IMG_8513_cut_4.tif   dorsal   
40113  CAM050036   26105_CAM050036_S1_9_HW_wt_IMG_8541_cut3.tif   dorsal   
40120  CAM050036  26116_CAM050036_S1_9_HW_wt_IMG_8541_cut_3.tif   dorsal   
11978  CAM010354                               23471_10354d.jpg   dorsal   
12010  CAM010362                               23484_10362v.jpg  ventral   

                  Taxonomic_Name            Locality  \
40141  Heliconius sara ssp. sara           Madingley   
40144  Heliconius sara ssp. sara           Madingley   
40112  Heliconius sara ssp. sara  Gamboa_insectaries   
40116  Heliconius sara ssp. sara  Gamboa_insectaries   
40138  Heliconius sara ssp. sara           Madingley   
40145  Heliconius sara ssp. sara           Madingley   
40113  Heliconius sara ssp. sara  Gamboa_insectaries   
40120  Heliconius sara ssp. sara  Gamboa_insectaries   
11978             Heliconius sp.                 NaN   
12010             Heliconius sp.                 NaN   

                                    md5  
40141  21e726df7076f5c13fe1441126bac4d5  
40144  21e726df7076f5c13fe1441126bac4d5  
40112  34adbd5596f977834fb2c6876d2f4493  
40116  34adbd5596f977834fb2c6876d2f4493  
40138  464801449aa127933d9619cb4e6f0a01  
40145  464801449aa127933d9619cb4e6f0a01  
40113  6d63d659fbc02369010938bbc229ad4d  
40120  6d63d659fbc02369010938bbc229ad4d  
11978  84d4ac6527458786cdb33166cd80e0a8  
12010  84d4ac6527458786cdb33166cd80e0a8

These have mismatched filenames and even mismatched CAMIDs for record 2552371.

The first 8 are all cropped close-ups of a single wing, so don't seem particularly helpful for our use-cases. Will keep the ones with `cut_` in the name, as some of this duplication seems to be from errors in image naming (the view also is inconsistent since it's a crop of a single wing).

The last two are unspecified species. The image is definitely dorsal, but there is no indication of which specimen it is, so both records must be removed.